In [2]:
from selenium import webdriver
from bs4 import BeautifulSoup
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time

df_final = []
# service = Service(executable_path="chromedriver")
# driver = webdriver.Chrome(service=service)
driver = webdriver.Chrome() # geht automatisch ab Selenium 4.6
wait = WebDriverWait(driver, 10)

url = "https://www.eqs-news.com/de/"
driver.get(url)

um_liste=['1&1 AG',
 'Aixtron SE',
 'Atoss Software AG',
 'Bechtle AG',
 'Cancom SE',
 'Carl Zeiss Meditec AG',
 'CompuGroup Medical SE',
 'Deutsche Telekom AG',
 'Eckert & Ziegler Strahlen- und Medizintechnik AG',
 'Elmos Semiconductor SE',
 'Evotec SE',
 'Formycon AG',
 'Freenet AG',
 'Hensoldt AG',
 'Infineon Technologies AG',
 'Ionos SE',
 'Jenoptik AG',
 'Kontron AG',
 'Nagarro SE',
 'Nemetschek SE',
 'Nordex SE',
 'PNE AG',
 'Qiagen N.V.',
 'SAP SE',
 'Sartorius AG',
 'Siemens Healthineers AG',
 'Siltronic AG',
 'Suss Microtec SE',
 'TeamViewer AG',
 'United Internet AG']

# Cookies zulassen
try:
    agree_btn = wait.until(EC.element_to_be_clickable((By.ID, "didomi-notice-agree-button")))
    agree_btn.click() # Cookies zulassen
except Exception as e:
    print(f"Cookie-Button nicht gefunden oder nicht klickbar: {e}")
    # Optional: Fahren Sie fort, falls der Banner nicht erscheint (z.B. weil Cookies bereits gesetzt sind)

# Hier ist ein statisches Warten (time.sleep) nach dem Klicken oft nicht mehr nötig,
# da der nächste Schritt normalerweise das Warten auf die geladenen Ergebnisse wäre.
# Ein kurzes time.sleep(1) kann aber manchmal sinnvoll sein, um dem Browser Zeit zu geben,
# die DOM-Änderung nach dem Klick abzuschließen, bevor man das nächste Element sucht.
time.sleep(3)


# Für jedes Unternehmen den Filter ausführen
for firma in um_liste:

    print(f"Filtere nach: {firma}")

    # 1. "Erweiterter Filter" öffnen
    try:
        filter_btn = wait.until(EC.element_to_be_clickable(
            (By.CSS_SELECTOR, "p.advanced-filter__button")
        ))
        filter_btn.click()
    except:
        print("Konnte 'Erweiterter Filter' nicht klicken.")
        continue


    # 2. Suchfeld finden -> Firmennamen eingeben
    try:
        textfeld = wait.until(EC.presence_of_element_located((By.ID, "filter_text")))
        textfeld.clear()
        textfeld.send_keys(firma)
    except:
        print("Suchfeld nicht gefunden.")

    if firma == "1&1 AG": # Nur beim ersten Mal da die Webseite sich daran erinnert
        # 3. Kategorie-Dropdown öffnen
        try:
            drpdwn_btn = wait.until(EC.element_to_be_clickable(
                (By.CSS_SELECTOR, "button.advanced-filter__dropdown-anchor")
            ))
            drpdwn_btn.click()
        except:
            print("Dropdown lässt sich nicht öffnen.")


        time.sleep(1)

        # 4. "Ad-hoc-Mitteilungen" auswählen
        try:
            ad_hoc_btn = wait.until(EC.element_to_be_clickable(
                (By.CSS_SELECTOR, "label[data-form-elem-id='ADHOC_filter_label']")
            ))
            ad_hoc_btn.click()
        except:
            print("Ad-hoc Label nicht gefunden.")
        time.sleep(1)

        # 5. Jahr 2025 wählen
        try:

            jahr_btn = wait.until(EC.element_to_be_clickable(
                (By.CSS_SELECTOR, ".select2-selection__arrow") # Achtung: Punkt vor dem Klassennamen
            ))
            jahr_btn.click()
            print("Dropdown geöffnet.")
        except Exception as e:
            print(f"Jahr-Button nicht gefunden: {e}")

        # 6. Option "2025" auswählen
        try:
            # KORREKTUR: Statt nach der ID zu suchen (die sich ändern kann),
            # sucht man nach dem Element, das den Text '2025' enthält und eine Option ist.
            # XPath Erklärung: Suche ein <li> Element, das die Klasse 'select2-results__option' hat UND den Text '2025'
            xpath_2025 = "//li[contains(@class, 'select2-results__option') and text()='2025']"

            btn_2025 = wait.until(EC.element_to_be_clickable(
                (By.XPATH, xpath_2025)
            ))
            btn_2025.click()
            print("Jahr 2025 ausgewählt.")
        except Exception as e:
           print(f"Option 2025 nicht gefunden: {e}")
    # 7. "Filter verwenden" klicken
    try:
        apply_btn = wait.until(EC.element_to_be_clickable(
            (By.ID, "search-advanced-filter")
        ))
        apply_btn.click()
    except:
        print("Apply-Button nicht klickbar.")
        continue

    # 8. Warten, bis Ergebnisse geladen sind
    time.sleep(2)

    # Übergang von Selenium an bs4
    html_text = driver.page_source
    soup = BeautifulSoup(html_text, 'html.parser')
    wrapper = soup.find("div", class_="news__list-wrapper")
    if not wrapper:
        print("Fehler: Konnte den 'news__list-wrapper' nicht finden.")
        exit()
    print(soup)

    # Daten extrahieren
    collected_data = []
    current_date = "Unbekannt"

    # Alle direkten Kinder durchgehen (Datum, Überschrift, News-Links)
    elements = wrapper.find_all(["p", "a", "li"])

    print(f"Verarbeite {len(elements)} Elemente...")
    for el in elements:

        # Prüfen, ob es eine Datums-Überschrift ist
        if "news__date" in el.get("class", []):
            current_date = el.get_text(strip=True) # z.B. "17 November 2025"

        # Prüfen, ob es eine Nachricht ist
        elif "news__list" in el.get("class", []):
            try:
                # Firma finden
                company_tag = el.find(class_="news__company")
                company = company_tag.get_text(strip=True) if company_tag else "Unbekannt"

                # Headline finden
                headline_tag = el.find(class_="news__heading")
                headline = headline_tag.get_text(strip=True) if headline_tag else "Keine Headline"

                # Link finden
                link = el.get("href", "")

                # Entweder auf die Links klicken, Text kopieren, zurück auf Homepage, bei nächstem Eintrag weitermachen, oder zuerst Links sammeln und eine neue Spalte ins DataFrame hinzufügen, in die die Texte kopiert werden sollten

                collected_data.append({
                    "Unternehmen": company,
                    "Überschrift": headline,
                    "Meldungstext": "Undefined", # Vorerst die Headline, da der Volltext auf der Unterseite liegt
                    "Datum": current_date,
                    "Link": link
                })

            except Exception as e:
                print(f"Fehler bei einem Element: {e}")

    if collected_data:
        df = pd.DataFrame(collected_data)
    else:
        print("Keine Nachrichten gefunden. Prüfen Sie die HTML-Struktur.")

    # Auf die einzelnen Links klicken und Texte extrahieren

    # HTML bereinigen
    def extract_clean_text(html_content):
        soup = BeautifulSoup(html_content, 'html.parser')

        # 1. Bilder entfernen
        for img in soup.find_all('img'):
            img.decompose() # Löscht das Tag komplett aus dem Baum

        # 2. Den Text-Container "news-details__content" finden
        content_div = soup.find('div', class_='news-details__content')

        # Fallback: Wenn keine spezielle Klasse da ist, nehmen wir den Body (wir filtern eh auf <p>)
        if not content_div:
            content_div = soup.body

        if not content_div:
            return "Fehler: Kein Inhalt gefunden"

        # 3. Alle Paragraphen <p> holen
        paragraphs = content_div.find_all('p')

        # Text extrahieren und zusammenfügen
        # get_text(strip=True) entfernt automatisch unnötige Leerzeichen am Anfang/Ende
        text_parts = [p.get_text(strip=True) for p in paragraphs]

        # Leere Strings filtern und mit Leerzeichen verbinden
        full_text = " ".join([t for t in text_parts if t])

        return full_text

    # Loop über das DataFrame
    print(f"Starte Download der Texte für {len(df)} Artikel...")

    for index, row in df.iterrows():
        link = row['Link']

        # Überspringen, falls kein Link da ist
        if not link or link == "Kein Link":
            continue

        print(f"[{index+1}/{len(df)}] Lade: {row['Unternehmen']}...")

        try:
            # 1. Seite laden
            driver.get(link)
            try:
                WebDriverWait(driver, 5).until(
                    EC.presence_of_element_located((By.TAG_NAME, "p"))
                )
            except:
                pass # Im Fall eines Timeouts es trotzdem mit dem Quelltext versuchen

            # 3. HTML an BeautifulSoup übergeben
            html = driver.page_source

            # 4. Text extrahieren & säubern
            clean_text = extract_clean_text(html)

            # 5. Ins DataFrame schreiben
            df.at[index, 'Meldungstext'] = clean_text

        except Exception as e:
            print(f"Fehler bei Index {index}: {e}")
            df.at[index, 'Meldungstext'] = "Fehler beim Download"

    # Browser schließen, wenn fertig
        print("\nFertig! Vorschau:")
        print(df[['Unternehmen', 'Meldungstext']].head())

    df_final.append(df)
    driver.get(url)

df_komplett = pd.concat(df_final, ignore_index=True)
df_komplett.to_csv("../raw/portfolio_data_final.csv", index=False, sep=";", encoding="utf-8-sig")
driver.quit()

Filtere nach: 1&1 AG
Dropdown geöffnet.
Jahr 2025 ausgewählt.
<html data-select2-id="38" lang="de-DE"><!-- EQS Group gestattet die Nutzung oder das Herunterladen von Inhalten dieser Website durch Dritte für die Entwicklung, das Training oder den Betrieb von künstlicher Intelligenz oder anderen maschinellen Lernsystemen ("Text und Data Mining") ausschließlich mit ausdrücklicher schriftlicher Zustimmung durch EQS Group. Ohne eine solche Zustimmung ist es untersagt, die Inhalte für Text und Data Mining zu verwenden. Dies gilt auch, wenn auf der Website keine Meta-Angaben vorhanden sind, die entsprechende Verfahren aussperren, und selbst dann, wenn Bots, die den Zweck haben, die Website zu Zwecken des Text und Data Mining auszulesen, nicht ausgesperrt werden. --><head>
<meta charset="utf-8"/>
<meta content="ie=edge" http-equiv="x-ua-compatible"/>
<meta content="width=device-width, initial-scale=1, user-scalable=yes, maximum-scale=3.0, shrink-to-fit=no" name="viewport"/>
<!-- <link rel="sho